# Transform IUPAC names into numerical data. Dopamine D1 receptor antagonists.

In [1]:
import pandas as pd

# Upload dataset as data frame
df_cids =pd.read_csv('df2_targets.csv', index_col=[0])

# To avoid truncation of some columns during data frame display
pd.set_option('display.max_columns', None) 

# Display the data frame
print('Shape of the data frame: ', df_cids.shape)
df_cids.head()

Shape of the data frame:  (49997, 2)


UPAC  target
0  N-[4-[2-(2-methoxyphenyl)ethylcarbamoyl]phenyl...       1
1  2-[4-cyclobutyl-1-[(4-ethoxyphenyl)methyl]pipe...       0
2  2-[[2-(2-methyl-N-methylsulfonylanilino)acetyl...       0
3  6-[(2E)-2-[(3-hydroxyphenyl)methylidene]hydraz...       0
4  2-[(2-phenyl-[1]benzofuro[3,2-d]pyrimidin-4-yl...       0

In [2]:
df_cids = df_cids.dropna()
df_cids.shape

(49997, 2)

In [3]:
df_cids = df_cids.drop_duplicates()
df_cids.shape

(49997, 2)

In [4]:
df_cids = df_cids[df_cids['UPAC'].notna()]
df_cids['UPAC'] = df_cids['UPAC'].astype('string') 
df_cids.dtypes

UPAC      string[python]
target             int64
dtype: object

In [5]:
# make a copy to use latter for connection aiwth smiles 
df_iupac_target = df_cids.copy()

In [6]:
# Obtain listo fo UPAC formulas provided in PubChem
UPAC_list = df_cids['UPAC'].to_list()

for item in UPAC_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

N-[4-[2-(2-methoxyphenyl)ethylcarbamoyl]phenyl]-2-methyl-2,3-dihydro-1,4-benzothiazine-4-carboxamide
2-[4-cyclobutyl-1-[(4-ethoxyphenyl)methyl]piperazin-2-yl]ethanol
2-[[2-(2-methyl-N-methylsulfonylanilino)acetyl]amino]benzoic acid
6-[(2E)-2-[(3-hydroxyphenyl)methylidene]hydrazinyl]-1H-pyrimidin-2-one
2-[(2-phenyl-[1]benzofuro[3,2-d]pyrimidin-4-yl)amino]acetic acid


In [7]:
from string import digits

# Remove elements from UPAC formulas
dataset = []
for i in UPAC_list:
    # Replace simbols with a coma
    new_list = i.translate(str.maketrans({'[': ' , ', ']': ' , ', 
                                         '(': ' , ', ')' : ' , ',
                                         '-': ' , ', ';' : ' , '}))
    
    new_str = new_list.translate(str.maketrans('', '', digits))
    dataset.append(new_str)
dataset

for item in dataset[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

N ,  ,  ,  ,  ,  ,  , methoxyphenyl , ethylcarbamoyl , phenyl ,  ,  , methyl , , , dihydro , , , benzothiazine ,  , carboxamide
 ,  ,  , cyclobutyl ,  ,  ,  ,  , ethoxyphenyl , methyl , piperazin ,  , yl , ethanol
 ,  ,  ,  ,  ,  , methyl , N , methylsulfonylanilino , acetyl , amino , benzoic acid
 ,  ,  , E ,  ,  ,  ,  ,  , hydroxyphenyl , methylidene , hydrazinyl ,  , H , pyrimidin ,  , one
 ,  ,  ,  , phenyl ,  ,  , benzofuro , , , d , pyrimidin ,  , yl , amino , acetic acid


In [8]:
# Convert the strings into list of strings
new_strings = []
for i in dataset:
    parsed_string = i.split(",")
    new_strings.append(parsed_string)
new_strings

for item in new_strings[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

['N ', '  ', '  ', '  ', '  ', '  ', '  ', ' methoxyphenyl ', ' ethylcarbamoyl ', ' phenyl ', '  ', '  ', ' methyl ', ' ', ' ', ' dihydro ', ' ', ' ', ' benzothiazine ', '  ', ' carboxamide']
[' ', '  ', '  ', ' cyclobutyl ', '  ', '  ', '  ', '  ', ' ethoxyphenyl ', ' methyl ', ' piperazin ', '  ', ' yl ', ' ethanol']
[' ', '  ', '  ', '  ', '  ', '  ', ' methyl ', ' N ', ' methylsulfonylanilino ', ' acetyl ', ' amino ', ' benzoic acid']
[' ', '  ', '  ', ' E ', '  ', '  ', '  ', '  ', '  ', ' hydroxyphenyl ', ' methylidene ', ' hydrazinyl ', '  ', ' H ', ' pyrimidin ', '  ', ' one']
[' ', '  ', '  ', '  ', ' phenyl ', '  ', '  ', ' benzofuro ', ' ', ' ', ' d ', ' pyrimidin ', '  ', ' yl ', ' amino ', ' acetic acid']


In [9]:
from functools import reduce
# Convert list of lists in one list 
new_list = reduce(lambda a, b: a + b, new_strings)

for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

N 
  
  
  
  


In [10]:
new_list = [s.replace(' ', '') for s in new_list]
for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

N






In [11]:
# Print the muber of left strings after reduction
print (len (new_list))

883591


In [12]:
# remove duplicates
from collections import OrderedDict

new_list = list(OrderedDict.fromkeys(new_list)) 

for item in new_list[:5]:  # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

N

methoxyphenyl
ethylcarbamoyl
phenyl


In [13]:
# Remove one letter strings
new_list_columns = [x for x in new_list if len(x) >= 4]

for item in new_list_columns[:5]:   # https://theprogrammingexpert.com/python-print-first-10-items-in-list/
    print(item)

methoxyphenyl
ethylcarbamoyl
phenyl
methyl
dihydro


In [14]:
print (len (new_list_columns))

4989


In [15]:
new_list_columns.sort()
new_list_columns

['acenaphthyleno',
 'acetamide',
 'acetamido',
 'acetamidoacetate',
 'acetamidoacetyl',
 'acetamidoacridin',
 'acetamidoadamantane',
 'acetamidoanilino',
 'acetamidobenzenesulfonate',
 'acetamidobenzoate',
 'acetamidobenzoyl',
 'acetamidocyclohexyl',
 'acetamidocyclopentane',
 'acetamidocyclopentanecarbonyl',
 'acetamidocyclopentyl',
 'acetamidodecanedioate',
 'acetamidoethyl',
 'acetamidoethylN',
 'acetamidoethylamino',
 'acetamidoethylcarbamoyl',
 'acetamidohexanoicacid',
 'acetamidomethyl',
 'acetamidophenoxy',
 'acetamidophenyl',
 'acetamidopiperidin',
 'acetamidopropane',
 'acetamidopropanoate',
 'acetamidopyridin',
 'acetamidothiadiazole',
 'acetate',
 'aceticacid',
 'acetohydrazide',
 'acetonitrile',
 'acetyl',
 'acetylanilino',
 'acetylbenzimidazol',
 'acetylbenzo',
 'acetylcarbamothioylamino',
 'acetylcarbamoyl',
 'acetylcarbamoylamino',
 'acetylchromen',
 'acetylhydrazinyl',
 'acetylimino',
 'acetylindol',
 'acetylnaphthalen',
 'acetyloxy',
 'acetyloxybenzoyl',
 'acetyloxyeth

In [16]:
import numpy as np

dict_func_groups = dict.fromkeys(new_list_columns, 0)
dict_func_groups

{'acenaphthyleno': 0,
 'acetamide': 0,
 'acetamido': 0,
 'acetamidoacetate': 0,
 'acetamidoacetyl': 0,
 'acetamidoacridin': 0,
 'acetamidoadamantane': 0,
 'acetamidoanilino': 0,
 'acetamidobenzenesulfonate': 0,
 'acetamidobenzoate': 0,
 'acetamidobenzoyl': 0,
 'acetamidocyclohexyl': 0,
 'acetamidocyclopentane': 0,
 'acetamidocyclopentanecarbonyl': 0,
 'acetamidocyclopentyl': 0,
 'acetamidodecanedioate': 0,
 'acetamidoethyl': 0,
 'acetamidoethylN': 0,
 'acetamidoethylamino': 0,
 'acetamidoethylcarbamoyl': 0,
 'acetamidohexanoicacid': 0,
 'acetamidomethyl': 0,
 'acetamidophenoxy': 0,
 'acetamidophenyl': 0,
 'acetamidopiperidin': 0,
 'acetamidopropane': 0,
 'acetamidopropanoate': 0,
 'acetamidopyridin': 0,
 'acetamidothiadiazole': 0,
 'acetate': 0,
 'aceticacid': 0,
 'acetohydrazide': 0,
 'acetonitrile': 0,
 'acetyl': 0,
 'acetylanilino': 0,
 'acetylbenzimidazol': 0,
 'acetylbenzo': 0,
 'acetylcarbamothioylamino': 0,
 'acetylcarbamoyl': 0,
 'acetylcarbamoylamino': 0,
 'acetylchromen': 0,


In [17]:
# https://stackoverflow.com/questions/28056171/how-to-build-and-fill-pandas-dataframe-from-for-loop
import copy
import re
dataset = []
data = []
# new_strings = []

list_formulas = df_cids['UPAC'].to_list()
for formula in list_formulas:
    new_list = re.findall(r'\b\w{4,}\b', formula)
    for group in new_list:
        # working
        new_dict = copy.deepcopy(dict_func_groups)
        for ii in new_list:
            if ii in new_dict.keys():
                new_dict[ii] +=1
                    
    id = formula
    # Combine all new features in an array
    # arr =[id, new_dict.values()]
    dataset.append(new_dict.values())

In [18]:
# Create an "index" column with the corresponding index values
df_iupac_target['index'] = df_iupac_target.index

# Display df_similarity
print('Shape of df_iupac_target ', df_iupac_target.shape)
df_iupac_target.head() 

Shape of df_iupac_target  (49997, 3)


UPAC  target  index
0  N-[4-[2-(2-methoxyphenyl)ethylcarbamoyl]phenyl...       1      0
1  2-[4-cyclobutyl-1-[(4-ethoxyphenyl)methyl]pipe...       0      1
2  2-[[2-(2-methyl-N-methylsulfonylanilino)acetyl...       0      2
3  6-[(2E)-2-[(3-hydroxyphenyl)methylidene]hydraz...       0      3
4  2-[(2-phenyl-[1]benzofuro[3,2-d]pyrimidin-4-yl...       0      4

In [19]:
df_func_groups = pd.DataFrame.from_dict(dataset,
                                        orient='columns',
                                        dtype=None, columns=None) 


df_func_groups.columns = new_list_columns
df_func_groups.head()

acenaphthyleno  acetamide  acetamido  acetamidoacetate  acetamidoacetyl  \
0               0          0          0                 0                0   
1               0          0          0                 0                0   
2               0          0          0                 0                0   
3               0          0          0                 0                0   
4               0          0          0                 0                0   

   acetamidoacridin  acetamidoadamantane  acetamidoanilino  \
0                 0                    0                 0   
1                 0                    0                 0   
2                 0                    0                 0   
3                 0                    0                 0   
4                 0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidocyclohexyl  acetamidocyclopentane  acetamidocyclopentanecarbonyl  \
0                    0                      0                              0   
1                    0                      0                              0   
2                    0                      0                              0   
3                    0                      0                              0   
4                    0                      0                              0   

   acetamidocyclopentyl  acetamidodecanedioate  acetamidoethyl  \
0                     0                      0               0   
1                     0                      0               0   
2                     0                      0               0   
3                     0                      0               0   
4                     0                      0               0   

   acetamidoethylN  acetamidoethylamino  acetamidoethylcarbamoyl  \
0                0                    0                        0   
1                0                    0                        0   
2                0                    0                        0   
3                0                    0                        0   
4                0                    0                        0   

   acetamidohexanoicacid  acetamidomethyl  acetamidophenoxy  acetamidophenyl  \
0                      0                0                 0                0   
1                      0                0                 0                0   
2                      0                0                 0                0   
3                      0                0                 0                0   
4                      0                0                 0                0   

   acetamidopiperidin  acetamidopropane  acetamidopropanoate  \
0                   0                 0                    0   
1                   0                 0                    0   
2                   0                 0                    0   
3                   0                 0                    0   
4                   0                 0                    0   

   acetamidopyridin  acetamidothiadiazole  acetate  aceticacid  \
0                 0                     0        0           0   
1                 0                     0        0           0   
2                 0                     0        0           0   
3                 0                     0        0           0   
4                 0                     0        0           0   

   acetohydrazide  acetonitrile  acetyl  acetylanilino  acetylbenzimidazol  \
0               0             0       0              0                   0   
1               0             0       0 

In [20]:
# Create an "index" column with the corresponding index values
df_func_groups['index'] = df_func_groups.index

# Convert the index values into strings
# df_func_groups['index'] = df_func_groups['index'].astype(str)

# Display df_similarity
print('Shape of df_func_groups: ', df_func_groups.shape)
df_func_groups.head() 

Shape of df_func_groups:  (49997, 4990)


acenaphthyleno  acetamide  acetamido  acetamidoacetate  acetamidoacetyl  \
0               0          0          0                 0                0   
1               0          0          0                 0                0   
2               0          0          0                 0                0   
3               0          0          0                 0                0   
4               0          0          0                 0                0   

   acetamidoacridin  acetamidoadamantane  acetamidoanilino  \
0                 0                    0                 0   
1                 0                    0                 0   
2                 0                    0                 0   
3                 0                    0                 0   
4                 0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidocyclohexyl  acetamidocyclopentane  acetamidocyclopentanecarbonyl  \
0                    0                      0                              0   
1                    0                      0                              0   
2                    0                      0                              0   
3                    0                      0                              0   
4                    0                      0                              0   

   acetamidocyclopentyl  acetamidodecanedioate  acetamidoethyl  \
0                     0                      0               0   
1                     0                      0               0   
2                     0                      0               0   
3                     0                      0               0   
4                     0                      0               0   

   acetamidoethylN  acetamidoethylamino  acetamidoethylcarbamoyl  \
0                0                    0                        0   
1                0                    0                        0   
2                0                    0                        0   
3                0                    0                        0   
4                0                    0                        0   

   acetamidohexanoicacid  acetamidomethyl  acetamidophenoxy  acetamidophenyl  \
0                      0                0                 0                0   
1                      0                0                 0                0   
2                      0                0                 0                0   
3                      0                0                 0                0   
4                      0                0                 0                0   

   acetamidopiperidin  acetamidopropane  acetamidopropanoate  \
0                   0                 0                    0   
1                   0                 0                    0   
2                   0                 0                    0   
3                   0                 0                    0   
4                   0                 0                    0   

   acetamidopyridin  acetamidothiadiazole  acetate  aceticacid  \
0                 0                     0        0           0   
1                 0                     0        0           0   
2                 0                     0        0           0   
3                 0                     0        0           0   
4                 0                     0        0           0   

   acetohydrazide  acetonitrile  acetyl  acetylanilino  acetylbenzimidazol  \
0               0             0       0              0                   0   
1               0             0       0 

In [21]:
# Add the new data frame df_similarity to the already existing df based on "index"
df = pd.merge(df_iupac_target,df_func_groups, on=['index'])

# Display df_similarity
print('Shape of df: ', df.shape)
df.head()

Shape of df:  (49997, 4992)


UPAC  target  index  \
0  N-[4-[2-(2-methoxyphenyl)ethylcarbamoyl]phenyl...       1      0   
1  2-[4-cyclobutyl-1-[(4-ethoxyphenyl)methyl]pipe...       0      1   
2  2-[[2-(2-methyl-N-methylsulfonylanilino)acetyl...       0      2   
3  6-[(2E)-2-[(3-hydroxyphenyl)methylidene]hydraz...       0      3   
4  2-[(2-phenyl-[1]benzofuro[3,2-d]pyrimidin-4-yl...       0      4   

   acenaphthyleno  acetamide  acetamido  acetamidoacetate  acetamidoacetyl  \
0               0          0          0                 0                0   
1               0          0          0                 0                0   
2               0          0          0                 0                0   
3               0          0          0                 0                0   
4               0          0          0                 0                0   

   acetamidoacridin  acetamidoadamantane  acetamidoanilino  \
0                 0                    0                 0   
1                 0                    0                 0   
2                 0                    0                 0   
3                 0                    0                 0   
4                 0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidocyclohexyl  acetamidocyclopentane  acetamidocyclopentanecarbonyl  \
0                    0                      0                              0   
1                    0                      0                              0   
2                    0                      0                              0   
3                    0                      0                              0   
4                    0                      0                              0   

   acetamidocyclopentyl  acetamidodecanedioate  acetamidoethyl  \
0                     0                      0               0   
1                     0                      0               0   
2                     0                      0               0   
3                     0                      0               0   
4                     0                      0               0   

   acetamidoethylN  acetamidoethylamino  acetamidoethylcarbamoyl  \
0                0                    0                        0   
1                0                    0                        0   
2                0                    0                        0   
3                0                    0                        0   
4                0                    0                        0   

   acetamidohexanoicacid  acetamidomethyl  acetamidophenoxy  acetamidophenyl  \
0                      0                0                 0                0   
1                      0                0                 0                0   
2                      0                0                 0                0   
3                      0                0                 0                0   
4                      0                0                 0                0   

   acetamidopiperidin  acetamidopropane  acetamidopropanoate  \
0                   0                 0                    0   
1                   0                 0                    0   
2                   0                 0                    0   
3                   0                 0                    0   
4                   0                 0                    0   

   acetamidopyridin  acetamidothiadiazole  acetate  aceticacid  \
0                 0                     0        0           0   
1                 0                     0        0           0   
2            

In [22]:
df.to_csv('df2_for_final.csv')

In [23]:
# Drop the CID and UPAC columns by name
df = df.drop(columns=['UPAC', 'index'],axis=1) 

In [24]:
# Display the data frame
print('Shape of the data frame: ', df.shape)
df.head()

Shape of the data frame:  (49997, 4990)


target  acenaphthyleno  acetamide  acetamido  acetamidoacetate  \
0       1               0          0          0                 0   
1       0               0          0          0                 0   
2       0               0          0          0                 0   
3       0               0          0          0                 0   
4       0               0          0          0                 0   

   acetamidoacetyl  acetamidoacridin  acetamidoadamantane  acetamidoanilino  \
0                0                 0                    0                 0   
1                0                 0                    0                 0   
2                0                 0                    0                 0   
3                0                 0                    0                 0   
4                0                 0                    0                 0   

   acetamidobenzenesulfonate  acetamidobenzoate  acetamidobenzoyl  \
0                          0                  0                 0   
1                          0                  0                 0   
2                          0                  0                 0   
3                          0                  0                 0   
4                          0                  0                 0   

   acetamidocyclohexyl  acetamidocyclopentane  acetamidocyclopentanecarbonyl  \
0                    0                      0                              0   
1                    0                      0                              0   
2                    0                      0                              0   
3                    0                      0                              0   
4                    0                      0                              0   

   acetamidocyclopentyl  acetamidodecanedioate  acetamidoethyl  \
0                     0                      0               0   
1                     0                      0               0   
2                     0                      0               0   
3                     0                      0               0   
4                     0                      0               0   

   acetamidoethylN  acetamidoethylamino  acetamidoethylcarbamoyl  \
0                0                    0                        0   
1                0                    0                        0   
2                0                    0                        0   
3                0                    0                        0   
4                0                    0                        0   

   acetamidohexanoicacid  acetamidomethyl  acetamidophenoxy  acetamidophenyl  \
0                      0                0                 0                0   
1                      0                0                 0                0   
2                      0                0                 0                0   
3                      0                0                 0                0   
4                      0                0                 0                0   

   acetamidopiperidin  acetamidopropane  acetamidopropanoate  \
0                   0                 0                    0   
1                   0                 0                    0   
2                   0                 0                    0   
3                   0                 0                    0   
4                   0                 0                    0   

   acetamidopyridin  acetamidothiadiazole  acetate  aceticacid  \
0                 0                     0        0           0   
1                 0                     0        0           0   
2                 0                     0        0           0   
3                 0                     0        0           0   
4                 0                     0        0           0   

   acetohydrazide  acetonitrile  acetyl  acetylanilino  acetylbenzimidazol  \
0               0             0       0              0                

In [25]:
df.to_csv('df2_targets_IUPACs.csv')